In [1]:
from pyspark.sql import SparkSession

from ts_train.ft2model.classification_training import ClassificationTraining
from ts_train.ft2model.training_helper import TrainingHelper

# Dataset reading and preparation 

In [2]:
spark = SparkSession.builder.getOrCreate()

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/09/21 15:19:30 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
23/09/21 15:19:31 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.


In [3]:
path_to_data = "../../../dataset_offline/ft2model/"

targets_df = spark.read.parquet(path_to_data + "target_pandas.parquet")
df = spark.read.parquet(path_to_data + "filtered_features.parquet").cache()

df = df.dropDuplicates(subset=['ID_CLIENTE_BIC'])
df = df.join(targets_df, on="ID_CLIENTE_BIC", how="left")

df.show()

23/09/21 15:19:33 WARN package: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


+--------------+-------------------------------------------------+----------------------------------------------------------+----------------------------------------------------------+----------------------------------------------------------+-----------------------------------------------------------+-------------------------------------------------+--------------------------------------------------+-------------------------------------------------+----------------------------------------+-----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------------+--------------------------------------------------+-------------------------------------------+-------------------------------------------------+----------------------------------------------------+--------------------------------------------+----------------------------------------------------+-----------------------------------------

In [4]:
features_cols_name = TrainingHelper.get_features_cols_name(df=df, excluded_cols_name=["ID_CLIENTE_BIC", "TARGET"])

In [5]:
train_df, test_df = TrainingHelper.train_test_split(df)

In [6]:
classification_training = ClassificationTraining(
    params={
        # "n_estimators": 1000,
        "max_depth": [3, 5, 7, 9],
        "min_child_weight": [1, 3, 5],
        "gamma": [0.0, 0.1, 0.2, 0.3, 0.4],
        "subsample": [0.6, 0.7, 0.8, 0.9],
        "colsample_bytree": [0.6, 0.7, 0.8, 0.9],
    },
    features_cols_name=features_cols_name,
    label_col_name="TARGET",
)

In [7]:
classification_training.fit(train_df)

[{Param(parent='SparkXGBClassifier_f5c94f67b748', name='max_depth', doc='Refer to XGBoost doc of xgboost.sklearn.XGBClassifier for this param max_depth'): 3, Param(parent='SparkXGBClassifier_f5c94f67b748', name='min_child_weight', doc='Refer to XGBoost doc of xgboost.sklearn.XGBClassifier for this param min_child_weight'): 1, Param(parent='SparkXGBClassifier_f5c94f67b748', name='gamma', doc='Refer to XGBoost doc of xgboost.sklearn.XGBClassifier for this param gamma'): 0.0, Param(parent='SparkXGBClassifier_f5c94f67b748', name='subsample', doc='Refer to XGBoost doc of xgboost.sklearn.XGBClassifier for this param subsample'): 0.6, Param(parent='SparkXGBClassifier_f5c94f67b748', name='colsample_bytree', doc='Refer to XGBoost doc of xgboost.sklearn.XGBClassifier for this param colsample_bytree'): 0.6}, {Param(parent='SparkXGBClassifier_f5c94f67b748', name='max_depth', doc='Refer to XGBoost doc of xgboost.sklearn.XGBClassifier for this param max_depth'): 3, Param(parent='SparkXGBClassifier_f

2023-09-21 15:19:39,271 INFO XGBoost-PySpark: _fit Running xgboost-2.0.0 on 1 workers with
	booster params: {'colsample_bytree': 0.6, 'device': 'cpu', 'gamma': 0.0, 'max_depth': 3, 'min_child_weight': 1, 'objective': 'binary:logistic', 'subsample': 0.6, 'nthread': 1}
	train_call_kwargs_params: {'verbose_eval': True, 'num_boost_round': 100}
	dmatrix_kwargs: {'nthread': 1, 'missing': 0.0}
[15:19:41] task 0 got new rank 0                                    (0 + 1) / 1]
2023-09-21 15:19:42,969 INFO XGBoost-PySpark: _fit Finished xgboost training!   
INFO:XGBoost-PySpark:Do the inference on the CPUs
INFO:XGBoost-PySpark:Do the inference on the CPUs
23/09/21 15:19:44 WARN GarbageCollectionMetrics: To enable non-built-in garbage collector(s) List(G1 Concurrent GC), users should configure it(them) to spark.eventLog.gcMetrics.youngGenerationGarbageCollectors or spark.eventLog.gcMetrics.oldGenerationGarbageCollectors
INFO:XGBoost-PySpark:Do the inference on the CPUs
INFO:XGBoost-PySpark:Do the i

In [ ]:
prediction_df = classification_training.predict(test_df)

In [ ]:
classification_training.score(prediction_df)